In [31]:
import numpy as np
import time

In [32]:
def triu_1( U, b ):

  n = b.shape[ 0 ]
  x = np.empty( b.shape )

  for i in range( n - 1, -1, -1 ):
    tmp = 0.0
    for j in range( i + 1, n ):
      tmp = tmp + U[ i, j ] * x[ j ]
    x[ i ] = ( b[ i ] - tmp ) / U[ i, i ]

  return x

In [50]:
n = 1000
U = np.random.normal( size = ( n, n ) ).astype( np.float32 )
for i in range( n ):
  for j in range( i ):
    U[ i, j ] = 0.0
U[ range( n ), range( n ) ] = U[ range( n ), range( n ) ] + 5.0 * np.sqrt( n )
b = np.random.normal( size = ( n, ) ).astype( np.float32 )

start = time.time()
x = triu_1( U, b )
end = time.time()
print( end - start )
t_1 = end - start

print( np.linalg.norm( U @ x - b ) )

1.4638419151306152
1.7165360440344537e-14


In [29]:
print( np.linalg.cond( U ) )

81.62477879007007


In [36]:
def triu_2( U, b ):

  n = b.shape[ 0 ]
  x = np.empty( b.shape )

  for i in range( n - 1, -1, -1 ):
    x[ i ] = ( b[ i ] - U[ i, i + 1 : ] @ x[ i + 1 : ] ) / U[ i, i ]

  return x

In [51]:
start = time.time()
x = triu_2( U, b )
end = time.time()
print( end - start )
t_2 = end - start

print( np.linalg.norm( U @ x - b ) )

0.02025294303894043
1.6694613182330644e-14


In [52]:
print( t_1 / t_2 )

72.27798509658963


In [55]:
def gauss_solve_1( A, b ):

  n = A.shape[ 0 ]

  for i in range( n ):
    for k in range( i + 1, n ):
      alpha = A[ k, i ] / A[ i, i ]
      for j in range( i, n ):
        A[ k, j ] = A[ k, j ] - alpha * A[ i, j ]
      b[ k ] = b[ k ] - alpha * b[ i ]
  
  x = triu_1( A, b )

  return x

In [56]:
A = np.array(
    [
        [ 1.0, 1.0, 1.0, 1.0 ],
        [ 1.0, 2.0, 3.0, 4.0 ],
        [ 1.0, 3.0, 4.0, 3.0 ],
        [ 1.0, 1.0, 0.0, 0.0 ]
    ]
)

b = np.array( [ 1.0, 2.0, 3.0, 4.0 ] )

x = gauss_solve_1( A.copy(), b.copy() )

print( A @ x )

[1. 2. 3. 4.]


In [84]:
n = 500

A = np.random.normal( size = ( n, n ) )
b = np.random.normal( size = ( n, ) )

start = time.time()
x = gauss_solve_1( A.copy(), b.copy() )
end = time.time()
t_1 = end - start

print( t_1 )
print( np.linalg.norm( A @ x - b ) )

25.328006505966187
5.186514203481974e-10


In [85]:
print( np.linalg.cond( A ) )

1171.351179029405


In [86]:
def gauss_solve_2( A, b ):

  n = A.shape[ 0 ]

  for i in range( n ):
    for k in range( i + 1, n ):
      alpha = A[ k, i ] / A[ i, i ]
      A[ k, i : ] = A[ k, i : ] - alpha * A[ i, i : ]
      b[ k ] = b[ k ] - alpha * b[ i ]
  
  x = triu_2( A, b )

  return x

In [87]:
start = time.time()
x = gauss_solve_2( A.copy(), b.copy() )
end = time.time()
t_2 = end - start

print( t_2 )
print( np.linalg.norm( A @ x - b ) )

0.9684271812438965
4.3522229675714344e-10


In [88]:
def gauss_solve_3( A, b ):

  n = A.shape[ 0 ]

  for i in range( n ):
    alpha = A[ i + 1 :, i ] / A[ i, i ]
    A[ i + 1 :, i : ] = A[ i + 1 :, i : ] - alpha.reshape( ( alpha.shape[ 0 ], 1 ) ) * A[ i, i : ]
    b[ i + 1 : ] = b[ i + 1 : ] - alpha * b[ i ]
  
  x = triu_2( A, b )

  return x

In [89]:
start = time.time()
x = gauss_solve_3( A.copy(), b.copy() )
end = time.time()
t_3 = end - start

print( t_3 )
print( np.linalg.norm( A @ x - b ) )

0.14435219764709473
4.3522229675714344e-10


In [90]:
print( t_2 / t_3 )

6.708780309749495


In [91]:
print( t_1 / t_3 )

175.4597915293737
